In [ ]:
!pip install data_loader

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/


In [ ]:
!pip install git+https://www.github.com/keras-team/keras-contrib.git

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
  Cloning https://www.github.com/keras-team/keras-contrib.git to /tmp/pip-req-build-aha4b9e2
  Running command git clone -q https://www.github.com/keras-team/keras-contrib.git /tmp/pip-req-build-aha4b9e2


In [ ]:
from keras_contrib.layers.normalization.instancenormalization import InstanceNormalization
from keras.layers import Input, Dense, Reshape, Flatten, Dropout, Concatenate
from keras.layers import BatchNormalization, Activation, ZeroPadding2D
from keras.layers.advanced_activations import LeakyReLU
from keras.layers.convolutional import UpSampling2D, Conv2D
from keras.models import Sequential, Model
from tensorflow.keras.optimizers import Adam
import datetime
import matplotlib.pyplot as plt
import sys
import numpy as np
import os
from imageio import imread
from glob import glob
import cv2




In [ ]:
class DataLoader():
    def __init__(self, dataset_name, img_res=(128, 128)):
        self.dataset_name = dataset_name
        self.img_res = img_res

    def load_data(self, domain, batch_size=4, is_testing=False):
        
        path = glob('/content/drive/MyDrive/%s/*/*.jpg' % (self.dataset_name))

        batch_images = np.random.choice(path, size=batch_size)

        imgs = []
        for img_path in batch_images:
            img = self.imread(img_path)
            if not is_testing:
                img = cv2.resize(src = img, dsize=self.img_res, interpolation = cv2.INTER_CUBIC )

                if np.random.random() > 0.5:
                    img = np.fliplr(img)
            else:
                img = cv2.resize(src = img, dsize=self.img_res, interpolation = cv2.INTER_CUBIC )
            imgs.append(img)

        imgs = np.array(imgs)/127.5 - 1.

        return imgs

    def load_batch(self, batch_size=1, is_testing=False):
        
        path_A = glob('/content/drive/MyDrive/person2citypop/person1/*.jpg' )
        path_B = glob('/content/drive/MyDrive/person2citypop/citypop1/*.jpg')

        self.n_batches = int(min(len(path_A), len(path_B)) / batch_size)
        total_samples = self.n_batches * batch_size

        # Sample n_batches * batch_size from each path list so that model sees all
        # samples from both domains
        path_A = np.random.choice(path_A, total_samples, replace=False)
        path_B = np.random.choice(path_B, total_samples, replace=False)

        for i in range(self.n_batches-1):
            batch_A = path_A[i*batch_size:(i+1)*batch_size]
            batch_B = path_B[i*batch_size:(i+1)*batch_size]
            imgs_A, imgs_B = [], []
            for img_A, img_B in zip(batch_A, batch_B):
                img_A = self.imread(img_A)
                img_B = self.imread(img_B)

                img_A = cv2.resize(src = img_A, dsize=self.img_res, interpolation = cv2.INTER_CUBIC )
                img_B = cv2.resize(src = img_B, dsize=self.img_res, interpolation = cv2.INTER_CUBIC )

                if not is_testing and np.random.random() > 0.5:
                        img_A = np.fliplr(img_A)
                        img_B = np.fliplr(img_B)

                imgs_A.append(img_A)
                imgs_B.append(img_B)

            imgs_A = np.array(imgs_A)/127.5 - 1.
            imgs_B = np.array(imgs_B)/127.5 - 1.

            yield imgs_A, imgs_B

    def load_img(self, path):
        img = self.imread(path)
        img = cv2.resize(src = img, dsize=self.img_res, interpolation = cv2.INTER_CUBIC )
        img = img/127.5 - 1.
        return img[np.newaxis, :, :, :]

    def imread(self, path):
        return imread(path, pilmode='RGB').astype(np.float)

In [ ]:
class CycleGAN():
    def __init__(self):
        # Input shape
        self.img_rows = 128
        self.img_cols = 128
        self.channels = 3
        self.img_shape = (self.img_rows, self.img_cols, self.channels)

        # Configure data loader
        self.dataset_name = 'person2citypop'
        self.data_loader = DataLoader(dataset_name=self.dataset_name,
                                      img_res=(self.img_rows, self.img_cols))

        # Calculate output shape of D (PatchGAN)
        patch = int(self.img_rows / 2**4)
        self.disc_patch = (patch, patch, 1)

        # Number of filters in the first layer of G and D
        self.gf = 32
        self.df = 64

        # Loss weights
        self.lambda_cycle = 3.5                    # Cycle-consistency loss
        self.lambda_id = 0.1 * self.lambda_cycle    # Identity loss

        optimizer = Adam(0.0002, 0.5)

        # Build and compile the discriminators
        self.d_A = self.build_discriminator()
        self.d_B = self.build_discriminator()
        self.d_A.compile(loss='mse',
            optimizer=optimizer,
            metrics=['accuracy'])
        self.d_B.compile(loss='mse',
            optimizer=optimizer,
            metrics=['accuracy'])

        # Construct Computational
        #   Graph of Generators
        # Build the generators
        self.g_AB = self.build_generator()
        self.g_BA = self.build_generator()

        # Input images from both domains
        img_A = Input(shape=self.img_shape)
        img_B = Input(shape=self.img_shape)

        # Translate images to the other domain
        fake_B = self.g_AB(img_A)
        fake_A = self.g_BA(img_B)
        # Translate images back to original domain
        reconstr_A = self.g_BA(fake_B)
        reconstr_B = self.g_AB(fake_A)
        # Identity mapping of images
        img_A_id = self.g_BA(img_A)
        img_B_id = self.g_AB(img_B)

        # For the combined model we will only train the generators
        self.d_A.trainable = False
        self.d_B.trainable = False

        # Discriminators determines validity of translated images
        valid_A = self.d_A(fake_A)
        valid_B = self.d_B(fake_B)

        #Combine model trains generators to fool discriminators
        self.combined = Model(inputs = [img_A, img_B],
        outputs = [valid_A, valid_B,
        reconstr_A, reconstr_B,
        img_A_id, img_B_id])

        self.combined.compile(loss=['mse','mse',
        'mae', 'mae',
        'mae', 'mae'],
        loss_weights = [1, 1,
        self.lambda_cycle, self.lambda_cycle,
        self.lambda_id, self.lambda_id],
        optimizer = optimizer)
    
    def build_generator(self):

        def conv2d(layer_input, filters, f_size=4):
            d = Conv2D(filters, kernel_size = f_size, strides = 2, padding = 'same')(layer_input)
            d = LeakyReLU(alpha=0.2)(d)
            d = InstanceNormalization()(d)
            return d

        def deconv2d(layer_input, skip_input, filters, f_size=4, dropout_rate=0):
            u = UpSampling2D(size=2)(layer_input)
            u = Conv2D(filters, kernel_size = f_size, strides=1, padding = 'same',activation='relu' )(u)
            if dropout_rate:
                u = Dropout(dropout_rate)(u)
            u = InstanceNormalization()(u)
            u = Concatenate()([u, skip_input])
            return u

        # Image input
        d0 = Input(shape = self.img_shape)


        #Downsampling
        d1 = conv2d(d0, self.gf)
        d2 = conv2d(d1, self.gf*2)
        d3 = conv2d(d2, self.gf*4)
        d4 = conv2d(d3, self.gf*8)

        #Upsampling
        u1 = deconv2d(d4, d3, self.gf*4)
        u2 = deconv2d(u1, d2, self.gf*2)
        u3 = deconv2d(u2, d1, self.gf)

        u4 = UpSampling2D(size = 2)(u3)
        output_img = Conv2D(self.channels, kernel_size = 4, strides = 1, padding = 'same', activation = 'tanh' )(u4)

        return Model(d0, output_img)

    def build_discriminator(self):

        def d_layer(layer_input, filters, f_size=4, normalization=True):
            d = Conv2D(filters, kernel_size = f_size, strides=2, padding='same')(layer_input)
            d = LeakyReLU(alpha=0.2)(d)
            if normalization:
                d = InstanceNormalization()(d)
            return d

        img = Input(shape=self.img_shape)

        d1 = d_layer(img, self.df, normalization=False)
        d2 = d_layer(d1, self.df*2)
        d3 = d_layer(d2, self.df*4)
        d4 = d_layer(d3, self.df*8)

        validity = Conv2D(1, kernel_size=4, strides=1, padding='same')(d4)

        return Model(img, validity)

    def train(self, epochs, batch_size=1, sample_interval=50):

        start_time = datetime.datetime.now()

        #Adverarial loss groud truths

        valid = np.ones((batch_size,) + self.disc_patch)
        fake = np.zeros((batch_size,) + self.disc_patch)

        for epoch in range(epochs):
            for batch_i, (imgs_A, imgs_B) in enumerate(self.data_loader.load_batch(batch_size)):

                #____________
                # Train Discriminators
                #---------------

                #Translate images to opposite domain
                fake_B = self.g_AB.predict(imgs_A)
                fake_A = self.g_BA.predict(imgs_B)

                #Train the discriminators (original images = real/ translated = Fake)
                dA_loss_real = self.d_A.train_on_batch(imgs_A, valid)
                dA_loss_fake = self.d_A.train_on_batch(fake_A, fake)
                dA_loss = 0.5 * np.add(dA_loss_real, dA_loss_fake)

                dB_loss_real = self.d_B.train_on_batch(imgs_B, valid)
                dB_loss_fake = self.d_B.train_on_batch(fake_B, fake)
                dB_loss = 0.5 * np.add(dA_loss_real, dB_loss_fake)

                #Total discriminator loss 
                d_loss = 0.5 * np.add(dA_loss, dB_loss)

                # Train Generators
                g_loss = self.combined.train_on_batch([imgs_A, imgs_B],
                [valid,valid,
                imgs_A, imgs_B,
                imgs_A, imgs_B])

                elasped_time = datetime.datetime.now() - start_time

                #Plot the progress 
                print("[Epoch %d%d] [Batch %d%d] [D loss: %f, acc: %3d%%] [G loss: %05f, adv: %05f, recon: %05f, id: %05f] time: %s" \
                    % (epoch, epochs,
                    batch_i, self.data_loader.n_batches,
                    d_loss[0], 100*d_loss[1],
                    g_loss[0],
                    np.mean(g_loss[1:3],),
                    np.mean(g_loss[3:5]),
                    np.mean(g_loss[5:6]),
                    elasped_time))

                # 인터벌 저장 -> 생성된 이미지 샘플들을 저장
                if batch_i % sample_interval == 0 :
                    self.sample_image(epoch, batch_i)

    def sample_image(self, epoch, batch_i):
        os.makedirs('trial(1)/%s'% self.dataset_name, exist_ok =True)
        r,c = 2,3

        imgs_A = self.data_loader.load_data(domain="A", batch_size=1, is_testing=True)
        imgs_B = self.data_loader.load_data(domain="B", batch_size=1, is_testing=True)

        # Translate images to the other domain
        fake_B = self.g_AB.predict(imgs_A)
        fake_A = self.g_BA.predict(imgs_B)
        # Translate back to original domain
        reconstr_A = self.g_BA.predict(fake_B)
        reconstr_B = self.g_AB.predict(fake_A)

        gen_imgs = np.concatenate([imgs_A, fake_B, reconstr_A, imgs_B, fake_A, reconstr_B])

        # Rescale images 0 - 1
        gen_imgs = 0.5 * gen_imgs + 0.5

        titles = ['Original', 'Translated', 'Reconstructed']
        fig, axs = plt.subplots(r, c)
        cnt = 0
        for i in range(r):
            for j in range(c):
                axs[i,j].imshow(gen_imgs[cnt])
                axs[i, j].set_title(titles[j])
                axs[i,j].axis('off')
                cnt += 1
        fig.savefig("trial(1)/%s/%d_%d.png" % (self.dataset_name, epoch, batch_i))
        plt.close()

        

In [ ]:
gan = CycleGAN()
gan.train(epochs=400, batch_size=1, sample_interval=200)

/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:71: DeprecationWarning: `np.float` is a deprecated alias for the builtin `float`. To silence this warning, use `float` by itself. Doing this will not modify any behavior and is safe. If you specifically wanted the numpy scalar type, use `np.float64` here.
Deprecated in NumPy 1.20; for more details and guidance: https://numpy.org/devdocs/release/1.20.0-notes.html#deprecations


[Epoch 0400] [Batch 0107] [D loss: 16.498013, acc:  27%] [G loss: 60.317028, adv: 26.921156, recon: 0.853716, id: 0.402151] time: 0:00:16.222980


Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).


[Epoch 0400] [Batch 1107] [D loss: 7.972948, acc:  76%] [G loss: 67.768654, adv: 30.145404, recon: 0.981095, id: 0.588875] time: 0:00:16.911985
[Epoch 0400] [Batch 2107] [D loss: 36.842701, acc:  16%] [G loss: 173.069061, adv: 82.720482, recon: 1.010782, id: 0.629905] time: 0:00:17.134532
[Epoch 0400] [Batch 3107] [D loss: 19.756400, acc:  71%] [G loss: 38.304642, adv: 15.415622, recon: 0.997854, id: 0.661702] time: 0:00:17.367385
[Epoch 0400] [Batch 4107] [D loss: 19.333948, acc:  21%] [G loss: 13.843156, adv: 2.244207, recon: 1.246524, id: 0.722954] time: 0:00:17.585998
[Epoch 0400] [Batch 5107] [D loss: 5.240233, acc:  71%] [G loss: 13.532980, adv: 3.378386, recon: 0.884656, id: 0.670697] time: 0:00:17.817253
[Epoch 0400] [Batch 6107] [D loss: 2.662827, acc:  51%] [G loss: 11.957878, adv: 2.292145, recon: 0.958726, id: 0.676153] time: 0:00:18.038914
[Epoch 0400] [Batch 7107] [D loss: 2.191998, acc:  37%] [G loss: 8.902700, adv: 1.004335, recon: 0.898805, id: 0.704421] time: 0:00:18.

Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).


...

[Epoch 397400] [Batch 1107] [D loss: 0.017453, acc: 100%] [G loss: 3.196301, adv: 1.022066, recon: 0.146274, id: 0.085064] time: 2:44:12.368077
[Epoch 397400] [Batch 2107] [D loss: 0.010521, acc: 100%] [G loss: 3.145557, adv: 1.037962, recon: 0.131240, id: 0.124486] time: 2:44:12.595191
[Epoch 397400] [Batch 3107] [D loss: 0.061878, acc: 100%] [G loss: 3.072586, adv: 0.937954, recon: 0.150578, id: 0.150055] time: 2:44:12.827383
[Epoch 397400] [Batch 4107] [D loss: 0.009153, acc: 100%] [G loss: 3.178345, adv: 0.976020, recon: 0.159423, id: 0.108881] time: 2:44:13.057877
[Epoch 397400] [Batch 5107] [D loss: 0.016481, acc: 100%] [G loss: 3.062300, adv: 1.019936, recon: 0.132035, id: 0.090067] time: 2:44:13.281864
[Epoch 397400] [Batch 6107] [D loss: 0.044936, acc:  99%] [G loss: 3.940873, adv: 1.195977, recon: 0.197927, id: 0.172117] time: 2:44:13.510951
[Epoch 397400] [Batch 7107] [D loss: 0.012948, acc: 100%] [G loss: 3.121237, adv: 0.993898, recon: 0.135259, id: 0.345708] time: 2:44:13

Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).


[Epoch 398400] [Batch 1107] [D loss: 0.032469, acc:  99%] [G loss: 3.215341, adv: 0.996656, recon: 0.158667, id: 0.090686] time: 2:44:36.972952
[Epoch 398400] [Batch 2107] [D loss: 0.037549, acc: 100%] [G loss: 3.235083, adv: 1.079720, recon: 0.134902, id: 0.107517] time: 2:44:37.196304
[Epoch 398400] [Batch 3107] [D loss: 0.025833, acc: 100%] [G loss: 2.920669, adv: 0.958037, recon: 0.124154, id: 0.076621] time: 2:44:37.430082
[Epoch 398400] [Batch 4107] [D loss: 0.007100, acc: 100%] [G loss: 3.215711, adv: 0.987192, recon: 0.151067, id: 0.183316] time: 2:44:37.656959
[Epoch 398400] [Batch 5107] [D loss: 0.027274, acc:  99%] [G loss: 3.507780, adv: 1.039358, recon: 0.171304, id: 0.172523] time: 2:44:37.897869
[Epoch 398400] [Batch 6107] [D loss: 0.007772, acc: 100%] [G loss: 3.583045, adv: 1.011486, recon: 0.197558, id: 0.110325] time: 2:44:38.113303
[Epoch 398400] [Batch 7107] [D loss: 0.023278, acc: 100%] [G loss: 3.676925, adv: 1.012343, recon: 0.214866, id: 0.106856] time: 2:44:38

Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).
Clipping input data to the valid range for imshow with RGB data ([0..1] for floats or [0..255] for integers).


[Epoch 399400] [Batch 1107] [D loss: 0.059523, acc:  96%] [G loss: 3.261619, adv: 0.962610, recon: 0.170425, id: 0.241612] time: 2:45:01.750923
[Epoch 399400] [Batch 2107] [D loss: 0.015616, acc: 100%] [G loss: 3.302983, adv: 1.042682, recon: 0.143599, id: 0.155768] time: 2:45:01.964875
[Epoch 399400] [Batch 3107] [D loss: 0.043778, acc: 100%] [G loss: 3.231771, adv: 1.014451, recon: 0.154110, id: 0.116098] time: 2:45:02.175891
[Epoch 399400] [Batch 4107] [D loss: 0.017767, acc: 100%] [G loss: 3.011847, adv: 1.014433, recon: 0.124257, id: 0.094857] time: 2:45:02.414849
[Epoch 399400] [Batch 5107] [D loss: 0.044875, acc:  98%] [G loss: 2.993784, adv: 0.945535, recon: 0.132008, id: 0.147267] time: 2:45:02.646944
[Epoch 399400] [Batch 6107] [D loss: 0.031095, acc: 100%] [G loss: 3.052744, adv: 0.981260, recon: 0.135527, id: 0.134844] time: 2:45:02.877672
[Epoch 399400] [Batch 7107] [D loss: 0.015466, acc: 100%] [G loss: 2.975161, adv: 1.040220, recon: 0.113564, id: 0.135108] time: 2:45:03